In [1]:
import io
import os
import zipfile
from pathlib import Path

import ee
import geopandas as gpd
import requests

from utils.mapping import create_geemap

In [2]:
ee.Authenticate()
ee.Initialize()

# Boundaries

The boundary for the Atlantic Forest was sourced from the Spatial Ecology and Conservation Lab (LEEC) using the consensual limit corresponding to the intersection of the limits reviewed by the study.

Citation:
Muylaert, R.L.; Vancine, M.H.; Bernardo, R.; Oshima, J.E.F.; Sobral-Souza, T.; Tonetti, V.R.; Niebuhr, B.B.; Ribeiro, M.C. 2018. Uma nota sobre os limites territoriais da Mata Atlântica. Oecologia Australis 22: 3. DOI: 10.4257/oeco.2018.2203.09

In [3]:
boundary_url = url = (
    "https://github.com/LEEClab/ATLANTIC-limits/raw/master/data/limites_integradores_wgs84_v1_2_0.zip"
)
geometry_folder = Path("../../geometries")
boundary_name = "ma_limite_consensual_muylaert_et_al_2018_wgs84"
boundary_folder = geometry_folder / "limites_integradores_wgs84_v1_2_0/"

In [ ]:
response = requests.get(url)
if response.status_code == 200:
    with zipfile.ZipFile(io.BytesIO(response.content)) as z:
        z.extractall(geometry_folder)
    print(f"Files are saved in {geometry_folder}")
else:
    print("Status code:", response.status_code)

In [12]:
# Keep only consensus boundary

for file_name in os.listdir(boundary_folder):
    # Check if the file name does not contain the required substring
    if "ma_limite_consensual_muylaert_et_al_2018_wgs84" not in file_name:
        # Delete the file
        file_path = os.path.join(boundary_folder, file_name)
        os.remove(file_path)

In [4]:
af_gdf = gpd.read_file(
    f"{boundary_folder}/ma_limite_consensual_muylaert_et_al_2018_wgs84.shp"
)
af_fc = ee.FeatureCollection(af_gdf.__geo_interface__)

# Forest Type

In [5]:
forest_type = ee.Image("COPERNICUS/Landcover/100m/Proba-V-C3/Global/2019").select(
    "forest_type"
)
forest_type

In [6]:
forest_type_clip = forest_type.clip(af_fc)

In [7]:
forest_type_clip

In [8]:
forest_type_filtered = forest_type_clip.updateMask(forest_type.neq(0))

In [21]:
forest_type_dict = {
    # "0 Unknown": "282828",
    "1 Evergreen needle leaf": "666000",
    "2 Evergreen broad leaf": "009900",
    "3 Deciduous needle leaf": "70663e",
    "4 Deciduous broad leaf": "a0dc00",
    "5 Mix of forest types": "929900",
}

In [12]:
import geemap

In [22]:
m = geemap.Map()
m.centerObject(af_fc)
m.addLayer(forest_type_filtered, {}, "Forest Type (Copernicus Land Cover)")
m.add_text("Made by Ilse Paniagua")
m.add_legend(title="", legend_dict=forest_type_dict)
m

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

![Atlantic Forest Forest Type](../../maps/)

# Carbon Density

Canopy Height: https://glad.umd.edu/dataset/gedi

In [30]:
canopy_height = (
    ee.ImageCollection("users/potapovpeter/GEDI_V27").select("GEDI_SAM_v27").median()
)

In [31]:
canopy_height_clip = canopy_height.clip(af_fc)

In [ ]:
create_geemap(
    image=canopy_height_clip,
    center_by=af_fc,
    data_viz={},
    map_title="Canopy Height",
    continuous=True,
)

EEException: reduce.median: Error in map(ID=GEDI_AUS_v27):
Image.select: Band pattern 'GEDI_SAM_v27' did not match any bands. Available bands: [b1]

# Precipitation

In [66]:
precipitation_collection = ee.ImageCollection("ECMWF/ERA5/MONTHLY")

In [67]:
precipitation_collection

In [68]:
precipitation = precipitation_collection.select("total_precipitation").median()

In [69]:
precipitation

In [75]:
precipitation_viz = {"palette": "GnBu", "min": 0, "max": 2}

In [76]:
create_geemap(
    image=precipitation,
    data_viz=precipitation_viz,
    map_title="Monthly Precipitation Median",
    center_by=af_2023,
)


Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

# Slope & Elevation

In [ ]:
#

# MapBiomas

The boundaries for the Atlantic Forest were sourced from MapBiomas.

The source for the map legends is [here](https://bosqueatlantico.mapbiomas.org/wp-content/uploads/sites/8/2023/11/Legend-Code_Bosque-Atl-Col-3.pdf)

“Proyecto MapBiomas Bosque Atlántico Trinacional – Colección 3 de la Serie Anual de Mapas de Cobertura y Uso del Suelo del Bosque Atlántico Trinacional, adquirido en 4 de febrero 2025 a través del [link](https://code.earthengine.google.com/?accept_repo=users%2Fmapbiomas%2Fuser-toolkit&scriptPath=users%2Fmapbiomas%2Fuser-toolkit%3Amapbiomas-user-toolkit-lulc.js)“

# 